# Resampling, Hyperparameter Tuning & Model Selection



## Load Library

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import LogisticRegression, LogisticRegressionCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

from sklearn.model_selection import train_test_split, StratifiedKFold, LeaveOneOut, RandomizedSearchCV, GridSearchCV
from sklearn.metrics import accuracy_score

## Load Dataset & Inspection

In [4]:
training_data = pd.read_csv("./dataset/GiveMeSomeCredit/Givcs-training.csv")
test_data = pd.read_csv("./dataset/GiveMeSomeCredit/cs-test.csv")

FileNotFoundError: [Errno 2] File b'./dataset/GiveMeSomeCredit/cs-training.csv' does not exist: b'./dataset/GiveMeSomeCredit/cs-training.csv'

In [2]:
# Membaca metadata
pd.read_excel("./dataset/GiveMeSomeCredit/Data Dictionary.xls")

FileNotFoundError: [Errno 2] No such file or directory: './dataset/GiveMeSomeCredit/Data Dictionary.xls'

**Training Data**

In [11]:
training_data.describe()

Unnamed: 0  SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  \
count  150000.000000     150000.000000                         150000.000000   
mean    75000.500000          0.066840                              6.048438   
std     43301.414527          0.249746                            249.755371   
min         1.000000          0.000000                              0.000000   
25%     37500.750000          0.000000                              0.029867   
50%     75000.500000          0.000000                              0.154181   
75%    112500.250000          0.000000                              0.559046   
max    150000.000000          1.000000                          50708.000000   

                 age  NumberOfTime30-59DaysPastDueNotWorse      DebtRatio  \
count  150000.000000                         150000.000000  150000.000000   
mean       52.295207                              0.421033     353.005076   
std        14.771866                              4.192781    2037.818523   
min         0.000000                              0.000000       0.000000   
25%        41.000000                              0.000000       0.175074   
50%        52.000000                              0.000000       0.366508   
75%        63.000000                              0.000000       0.868254   
max       109.000000                             98.000000  329664.000000   

       MonthlyIncome  NumberOfOpenCreditLinesAndLoans  \
count   1.202690e+05                    150000.000000   
mean    6.670221e+03                         8.452760   
std     1.438467e+04                         5.145951   
min     0.000000e+00                         0.000000   
25%     3.400000e+03                         5.000000   
50%     5.400000e+03                         8.000000   
75%     8.249000e+03                        11.000000   
max     3.008750e+06                        58.000000   

       NumberOfTimes90DaysLate  NumberRealEstateLoansOrLines  \
count            150000.000000                 150000.000000   
mean                  0.265973                      1.018240   
std                   4.169304                      1.129771   
min                   0.000000                      0.000000   
25%                   0.000000                      0.000000   
50%                   0.000000                      1.000000   
75%                   0.000000                      2.000000   
max                  98.000000                     54.000000   

       NumberOfTime60-89DaysPastDueNotWorse  NumberOfDependents  
count                         150000.000000       146076.000000  
mean                               0.240387            0.757222  
std                                4.155179            1.115086  
min                                0.000000            0.000000  
25%                                0.000000            0.000000  
50%                                0.000000            0.000000  
75%                                0.000000            1.000000  
max                               98.000000           20.000000

In [14]:
training_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150000 entries, 0 to 149999
Data columns (total 12 columns):
Unnamed: 0                              150000 non-null int64
SeriousDlqin2yrs                        150000 non-null int64
RevolvingUtilizationOfUnsecuredLines    150000 non-null float64
age                                     150000 non-null int64
NumberOfTime30-59DaysPastDueNotWorse    150000 non-null int64
DebtRatio                               150000 non-null float64
MonthlyIncome                           120269 non-null float64
NumberOfOpenCreditLinesAndLoans         150000 non-null int64
NumberOfTimes90DaysLate                 150000 non-null int64
NumberRealEstateLoansOrLines            150000 non-null int64
NumberOfTime60-89DaysPastDueNotWorse    150000 non-null int64
NumberOfDependents                      146076 non-null float64
dtypes: float64(4), int64(8)
memory usage: 13.7 MB


In [15]:
training_data.isna().sum()

Unnamed: 0                                  0
SeriousDlqin2yrs                            0
RevolvingUtilizationOfUnsecuredLines        0
age                                         0
NumberOfTime30-59DaysPastDueNotWorse        0
DebtRatio                                   0
MonthlyIncome                           29731
NumberOfOpenCreditLinesAndLoans             0
NumberOfTimes90DaysLate                     0
NumberRealEstateLoansOrLines                0
NumberOfTime60-89DaysPastDueNotWorse        0
NumberOfDependents                       3924
dtype: int64

**Test Data**

In [16]:
test_data.describe()

Unnamed: 0  SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  \
count  101503.000000               0.0                         101503.000000   
mean    50752.000000               NaN                              5.310000   
std     29301.536524               NaN                            196.156039   
min         1.000000               NaN                              0.000000   
25%     25376.500000               NaN                              0.030131   
50%     50752.000000               NaN                              0.152586   
75%     76127.500000               NaN                              0.564225   
max    101503.000000               NaN                          21821.000000   

                 age  NumberOfTime30-59DaysPastDueNotWorse      DebtRatio  \
count  101503.000000                         101503.000000  101503.000000   
mean       52.405436                              0.453770     344.475020   
std        14.779756                              4.538487    1632.595231   
min        21.000000                              0.000000       0.000000   
25%        41.000000                              0.000000       0.173423   
50%        52.000000                              0.000000       0.364260   
75%        63.000000                              0.000000       0.851619   
max       104.000000                             98.000000  268326.000000   

       MonthlyIncome  NumberOfOpenCreditLinesAndLoans  \
count   8.140000e+04                    101503.000000   
mean    6.855036e+03                         8.453514   
std     3.650860e+04                         5.144100   
min     0.000000e+00                         0.000000   
25%     3.408000e+03                         5.000000   
50%     5.400000e+03                         8.000000   
75%     8.200000e+03                        11.000000   
max     7.727000e+06                        85.000000   

       NumberOfTimes90DaysLate  NumberRealEstateLoansOrLines  \
count            101503.000000                 101503.000000   
mean                  0.296691                      1.013074   
std                   4.515859                      1.110253   
min                   0.000000                      0.000000   
25%                   0.000000                      0.000000   
50%                   0.000000                      1.000000   
75%                   0.000000                      2.000000   
max                  98.000000                     37.000000   

       NumberOfTime60-89DaysPastDueNotWorse  NumberOfDependents  
count                         101503.000000        98877.000000  
mean                               0.270317            0.769046  
std                                4.503578            1.136778  
min                                0.000000            0.000000  
25%                                0.000000            0.000000  
50%                                0.000000            0.000000  
75%                                0.000000            1.000000  
max                               98.000000           43.000000

In [17]:
test_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101503 entries, 0 to 101502
Data columns (total 12 columns):
Unnamed: 0                              101503 non-null int64
SeriousDlqin2yrs                        0 non-null float64
RevolvingUtilizationOfUnsecuredLines    101503 non-null float64
age                                     101503 non-null int64
NumberOfTime30-59DaysPastDueNotWorse    101503 non-null int64
DebtRatio                               101503 non-null float64
MonthlyIncome                           81400 non-null float64
NumberOfOpenCreditLinesAndLoans         101503 non-null int64
NumberOfTimes90DaysLate                 101503 non-null int64
NumberRealEstateLoansOrLines            101503 non-null int64
NumberOfTime60-89DaysPastDueNotWorse    101503 non-null int64
NumberOfDependents                      98877 non-null float64
dtypes: float64(5), int64(7)
memory usage: 9.3 MB


In [18]:
test_data.isna().sum()

Unnamed: 0                                   0
SeriousDlqin2yrs                        101503
RevolvingUtilizationOfUnsecuredLines         0
age                                          0
NumberOfTime30-59DaysPastDueNotWorse         0
DebtRatio                                    0
MonthlyIncome                            20103
NumberOfOpenCreditLinesAndLoans              0
NumberOfTimes90DaysLate                      0
NumberRealEstateLoansOrLines                 0
NumberOfTime60-89DaysPastDueNotWorse         0
NumberOfDependents                        2626
dtype: int64

In [20]:
training_data = training_data.iloc[:,1:]

test_data = test_data.iloc[:,2:]

In [55]:
training_data['MonthlyIncome'] = training_data['MonthlyIncome'].fillna(training_data['MonthlyIncome'].median(skipna=True))

In [53]:
training_data['NumberOfDependents'] = training_data['NumberOfDependents'].fillna(0)

In [56]:
training_data.isna().sum()

SeriousDlqin2yrs                        0
RevolvingUtilizationOfUnsecuredLines    0
age                                     0
NumberOfTime30-59DaysPastDueNotWorse    0
DebtRatio                               0
MonthlyIncome                           0
NumberOfOpenCreditLinesAndLoans         0
NumberOfTimes90DaysLate                 0
NumberRealEstateLoansOrLines            0
NumberOfTime60-89DaysPastDueNotWorse    0
NumberOfDependents                      0
dtype: int64

## Resampling & Cross-Validation

Beberapa metode resampling yang dapat digunakan diantaranya adalah:

- Hold-out Validation
- K-Fold Cross-Validation
- Leave-One-Out Validation


### Hold-Out

Pada metode hold-out, data dipisah menjadi data training dan data validasi

![Hold-Out](./images/holdout.png)

Sumber gambar: https://machine-learning-course.readthedocs.io/en/latest/content/overview/crossvalidation.html

In [57]:
data_train = training_data.groupby("SeriousDlqin2yrs", group_keys=False).apply(lambda x: x.sample(frac=0.8, random_state=1000))

data_train

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
96384                  0                              0.270098   68   
16538                  0                              0.098004   58   
14062                  0                              0.284938   63   
125815                 0                              0.365282   51   
101835                 0                              0.534208   47   
16030                  0                              0.000000   42   
114711                 0                              0.654947   40   
47723                  0                              0.309392   55   
42726                  0                              0.016328   56   
39880                  0                              0.035908   42   
18430                  0                              1.000000   54   
11806                  0                              1.000000   38   
9942                   0                              1.322356   31   
9194                   0                              0.000355   55   
63071                  0                              0.001019   44   
117080                 0                              0.118610   49   
96160                  0                              1.000000   24   
32471                  0                              0.292120   47   
39660                  0                              0.019955   60   
137765                 0                              0.019258   55   
137899                 0                              0.061894   62   
92583                  0                              0.549005   48   
68337                  0                              0.706845   69   
1116                   0                              0.008000   65   
52802                  0                              0.052746   60   
92428                  0                              0.025861   78   
146482                 0                              0.000000   24   
116496                 0                              1.000000   57   
126060                 0                              1.000000   92   
80056                  0                              0.023923   70   
...                  ...                                   ...  ...   
113784                 1                              1.263473   37   
116454                 1                              0.456204   53   
19652                  1                              1.028455   48   
59728                  1                              0.044738   33   
45791                  1                              0.970515   51   
18300                  1                              0.761561   65   
107441                 1                              0.207983   27   
75585                  1                              1.000000   67   
35270                  1                              0.298805   39   
144282                 1                              1.000000   24   
107883                 1                              0.004701   66   
115544                 1                              0.065781   63   
141148                 1                              0.465445   27   
17945                  1                              1.000000   46   
80641                  1                              1.000000   35   
54248                  1                              0.831461   30   
121485                 1                              0.403113   50   
38789                  1                              0.316014   50   
104208                 1                              1.000000   47   
86169                  1                              0.876448   26   
4890                   1                              0.000000   60   
29873                  1                              1.000000   56   
71733                  1                              1.000000   43   
67352                  1                              0.157821   63   
6493                   1        

In [58]:
data_validasi = training_data.drop(data_train.index)

data_validasi

SeriousDlqin2yrs  RevolvingUtilizationOfUnsecuredLines  age  \
12                     0                              0.010352   46   
18                     0                              0.221813   43   
19                     0                              0.602794   25   
21                     1                              0.025656   38   
22                     0                              1.000000   39   
27                     0                              0.034421   69   
29                     0                              0.392995   58   
36                     0                              0.881836   50   
40                     0                              0.719985   41   
48                     0                              0.834048   38   
55                     0                              0.070854   55   
56                     0                              0.454972   46   
70                     0                              0.265898   36   
85                     0                              0.000000   58   
95                     0                              0.245353   37   
99                     0                              0.032618   75   
107                    0                              0.635415   32   
109                    0                              0.041258   61   
118                    0                              0.007521   68   
125                    0                              0.003722   58   
130                    0                              0.175728   43   
134                    0                              0.047312   51   
138                    0                              0.093962   55   
140                    0                              0.147996   55   
144                    0                              0.116677   31   
148                    0                              0.546999   50   
150                    0                              0.000000   48   
152                    0                              0.050790   30   
156                    0                              0.121557   58   
158                    0                              0.147712   40   
...                  ...                                   ...  ...   
149859                 0                              0.174702   62   
149861                 0                              0.089997   61   
149866                 0                              0.000884   47   
149867                 0                              0.753741   61   
149868                 0                              0.073332   32   
149869                 0                              0.652335   50   
149870                 0                              0.030994   59   
149872                 0                              0.364659   54   
149883                 0                              0.004145   48   
149884                 0                              0.806045   51   
149888                 0                              0.270734   48   
149891                 0                              0.960816   26   
149899                 0                              0.235331   46   
149902                 0                              0.000000   80   
149913                 0                              0.045998   39   
149922                 0                              0.761465   41   
149927                 0                              3.603566   71   
149930                 0                              0.000000   70   
149936                 0                              0.326193   66   
149938                 0                              0.329479   35   
149945                 0                              0.151670   50   
149947                 0                              0.220232   67   
149952                 0                              0.019785   58   
149957                 0                              0.843904   28   
149958                 0        

**Menggunakan Scikit-Learn train_test_split**

In [59]:
nilai_X = training_data.iloc[:,1:].values
nilai_y = training_data['SeriousDlqin2yrs'].values

X_train, X_val, y_train, y_val = train_test_split(nilai_X, nilai_y, test_size=0.2, stratify=nilai_y)

In [60]:
print("Ukuran X_train: ", X_train.shape)
print("Ukuran y_train: ", y_train.shape)
print("Ukuran X_val: ", X_val.shape)
print("Ukuran y_val: ", y_val.shape)

Ukuran X_train:  (120000, 10)
Ukuran y_train:  (120000,)
Ukuran X_val:  (30000, 10)
Ukuran y_val:  (30000,)


### K-Fold

Pada metode K-Fold, data dibagi menjadi data training dan data validasi dengan mengulang-ulang metode hold-out sebanyak k-kali. Hal ini berfungsi untuk mengurangi bias pada model.

![Kfold](./images/kfold.png)

Sumber gambar: https://machine-learning-course.readthedocs.io/en/latest/content/overview/crossvalidation.html#holdout-method

In [61]:
folding = StratifiedKFold(n_splits=10)

folding.get_n_splits(nilai_X, nilai_y)

10

In [62]:
for training_index, test_index in folding.split(nilai_X, nilai_y):
    print("Index X: ", training_index, " dan Index y: ", test_index)

Index X:  [ 14969  14970  14971 ... 149997 149998 149999]  dan Index y:  [    0     1     2 ... 15629 15662 15667]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [14969 14970 14971 ... 30887 30945 30986]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [29933 29934 29935 ... 45001 45002 45003]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [44997 45004 45005 ... 60047 60053 60075]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [59998 59999 60000 ... 75273 75291 75293]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [74984 74985 74986 ... 90962 91011 91036]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [ 89947  89948  89950 ... 105189 105218 105221]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index y:  [104988 104990 104991 ... 120572 120576 120577]
Index X:  [     0      1      2 ... 149997 149998 149999]  dan Index

### Leave-One-Out

Pada metode leave-one-out, data dibagi menjadi 2 layaknya hold-out, perbedaannya adalah yang dipakai menjadi data validasi hanya 1 baris/record data saja.

![Leave-One-Out](./images/lou.png)

Sumber gambar: https://medium.com/datadriveninvestor/k-fold-and-other-cross-validation-techniques-6c03a2563f1e

In [39]:
buang_atu = LeaveOneOut()

buang_atu.get_n_splits(nilai_X)

150000

In [40]:
for training_index, test_index in buang_atu.split(nilai_X):
    print("Fold ke")
    print("Ukuran X: ", training_index.shape, " dan ukuran y: ", test_index.shape)
    print("")

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

...

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y:  (1,)
Ukuran X:  (149999,)  dan ukuran y

## Hyperparameter Tuning

Terdapat dua metode yang paling umum untuk mencari model mana yang paling optimal tergantung dari seberapa baik performanya, yaitu:

- Metode Grid Search
- Metode Random Search

![Hyperparameter Tuning](./images/evaluate_overview.png)

**Inisiasi Grid**

In [67]:
# menentukan jumlah estimator
n_estimators = [10, 20]
# Menentukan jumlah feature yang digunakan dalam tiap split
max_features = ['auto', 'sqrt']
# Menentukan tingkat kedalaman pohon keputusan
max_depth = [5, 6, 7, 8]
# Menentukan jumlah minimum sampel untuk melakukan split pada node
min_samples_split = [2, 5, 10]
# Menentukan jumlah sampel minimum untuk melakukan split pada leaf
min_samples_leaf = [1, 2, 4]
# Metode penentuan sampling
bootstrap = [True, False]

# inisiasi grid
inisiasi_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf,
               'bootstrap': bootstrap}

inisiasi_grid

{'n_estimators': [10, 20],
 'max_features': ['auto', 'sqrt'],
 'max_depth': [5, 6, 7, 8],
 'min_samples_split': [2, 5, 10],
 'min_samples_leaf': [1, 2, 4],
 'bootstrap': [True, False]}

### Random Search

Random Search akan mencari parameter optimal secara acak tanpa harus mencoba semua kombinasi nilai.

**Inisiasi Model RandomForest**

In [64]:
model_random_forest = RandomForestClassifier()

In [68]:
model_random_cv = RandomizedSearchCV(estimator=model_random_forest, 
                                     param_distributions=inisiasi_grid,
                                     n_iter=5,
                                     cv=3,
                                    random_state=1000,
                                    n_jobs=2)

model_random_cv.fit(X_train,y_train)

RandomizedSearchCV(cv=3, error_score='raise-deprecating',
                   estimator=RandomForestClassifier(bootstrap=True,
                                                    class_weight=None,
                                                    criterion='gini',
                                                    max_depth=None,
                                                    max_features='auto',
                                                    max_leaf_nodes=None,
                                                    min_impurity_decrease=0.0,
                                                    min_impurity_split=None,
                                                    min_samples_leaf=1,
                                                    min_samples_split=2,
                                                    min_weight_fraction_leaf=0.0,
                                                    n_estimators='warn',
                                                    n_jobs=None

In [69]:
model_random_cv.best_estimator_

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=8, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=10,
                       min_weight_fraction_leaf=0.0, n_estimators=20,
                       n_jobs=None, oob_score=False, random_state=None,
                       verbose=0, warm_start=False)

In [71]:
hasil_prediksi = model_random_cv.predict(X_val)

hasil_prediksi

array([0, 0, 0, ..., 0, 0, 0])

In [73]:
accuracy_score(y_val, hasil_prediksi)

0.9374

## Grid Search

Grid Search akan mencari parameter optimal secara greedy.

In [74]:
model_grid_cv = GridSearchCV(estimator=model_random_forest, 
                                 param_grid=inisiasi_grid, 
                                 cv=folding, 
                                 n_jobs=3)

model_grid_cv.fit(X_train, y_train)

KeyboardInterrupt: 